In [1]:
# загрузка данных
from zipfile import ZipFile

PATH_TO_DATA = 'data.zip'

zip_data = ZipFile(PATH_TO_DATA)
filenames = [filename.filename for filename in zip_data.infolist()]
filenames[:2]

['data/', 'data/00e58afe-3ef5-42a6-92f3-8ee7abf868e1.json']

In [2]:
# посмотрим содержимое одного json файла
import json
json.loads(zip_data.read(filenames[1]))

[{'id': '60229527',
  'text': 'Curraghglass, an Anglicisation of the Gaelic, ‘Currach Glas’ meaning The Green Moor, is a townland in the civil parish of Templeport, County Cavan, Ireland. It lies in the Roman Catholic parish of Glangevlin and barony of Tullyhaw. Road at Curraghglass (geograph 3586592) ==Geography== Curraghglass is bounded on the north by Garvalt Lower and Gub (Glangevlin) townlands, on the west by Altshallan, Carrick West and Knockgorm townlands, on the south by Legatraghta and Moneensauran townlands and on the east by Tullynacross (Glangevlin) townland. Its chief geographical features are the Owenmore River (County Cavan), mountain streams, waterfalls, gravel pits and spring wells. The townland is traversed by minor public roads and rural lanes. The townland covers 175 statute acres. ==History== In earlier times the townland was probably uninhabited as it consists mainly of bog and poor clay soils. It was not seized by the English during the Plantation of Ulster in 16

In [3]:
# посмотрим на таблицу из одного json
import pandas as pd
file_content = json.loads(zip_data.read(filenames[1]))
data_from_dict = pd.DataFrame(file_content)
data_from_dict.head(5)

id                                               text  \
0  60229527  Curraghglass, an Anglicisation of the Gaelic, ...   
1  60229537  Anthony Joshua vs. Andy Ruiz Jr. was a heavywe...   
2  60229541  The men's freestyle welterweight competition a...   
3  60229580  The Munich-Montserrat Book of Hours is a 1535 ...   
4  60229585  Valdó Szűcs (born 29 June 1995) is a Hungarian...   

                                               title  
0                                       Curraghglass  
1                   Anthony Joshua vs. Andy Ruiz Jr.  
2  Wrestling at the 1956 Summer Olympics – Men's ...  
3                    Munich-Montserrat Book of Hours  
4                                        Valdó Szűcs

In [4]:
# сделаем так для каждого файла в архиве
data_list = list()
for filename in filenames:
    # некоторые файлы могут быть пустыми
    # добавим проверку
    text_content = zip_data.read(filename)
    if len(text_content):
        file_content = json.loads(text_content)
        data_from_dict = pd.DataFrame(file_content)
        data_list.append(data_from_dict)
    else:
        continue

# и склеим все таблички в одну
data = pd.concat(data_list, ignore_index=True)
data.head(5)

id                                               text  \
0  60229527  Curraghglass, an Anglicisation of the Gaelic, ...   
1  60229537  Anthony Joshua vs. Andy Ruiz Jr. was a heavywe...   
2  60229541  The men's freestyle welterweight competition a...   
3  60229580  The Munich-Montserrat Book of Hours is a 1535 ...   
4  60229585  Valdó Szűcs (born 29 June 1995) is a Hungarian...   

                                               title  
0                                       Curraghglass  
1                   Anthony Joshua vs. Andy Ruiz Jr.  
2  Wrestling at the 1956 Summer Olympics – Men's ...  
3                    Munich-Montserrat Book of Hours  
4                                        Valdó Szűcs

In [5]:
data.shape

(24661, 3)

In [6]:
# отбросим лишнее из датафрейма
data.drop(columns=['id', 'title'], inplace=True)
data.head(5)

text
0  Curraghglass, an Anglicisation of the Gaelic, ...
1  Anthony Joshua vs. Andy Ruiz Jr. was a heavywe...
2  The men's freestyle welterweight competition a...
3  The Munich-Montserrat Book of Hours is a 1535 ...
4  Valdó Szűcs (born 29 June 1995) is a Hungarian...

In [7]:
# диапазон для киррилического алфавита в нижнем регистре
sorted(list("абвгдаеёжзийклмнопрстуфхцчшщьъыэюя".encode("utf-8")))

[128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 145,
 176,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,
 185,
 186,
 187,
 188,
 189,
 190,
 191,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 208,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209,
 209]

In [8]:
# диапазон для латинского алфавита в нижнем регистре
sorted(list("abcdefghijklmnopqrstuvwxyz".encode("utf-8")))

[97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122]

Кириллические символы в кодировке Unicode лежат в диапазоне от 128 до 209.

In [9]:
# удаление пунктуации, служебных символов
# конвертация чисел в слова
def remove_punct(text):
    import string
    # удаляем пунктуацию и  
    # склеиваем символы, приводя слова к нижнему регистру
    return ''.join([c for c in text if c not in string.punctuation and (c.isalnum() or c == ' ')]).lower()

def numbers_to_words(text):
    import re
    from num2words import num2words
    # конвертируем числа в строки
    words = text.split()
    for i, word in enumerate(words):
        if re.match(r'\d+', word):
            try:
                words[i] = num2words(int(word), lang='en')
            except ValueError:
                pass
    return ' '.join(words)

def remove_tags(text):
    import re
    # удаление тегов разметки
    text = re.sub(r"<[^>]+>", "", str(text), flags=re.S)
    # удаление последовательностей \r и \n
    text = re.sub(r"\r|\n", " ", str(text), flags=re.S)
    # удаление последовательностей \b
    text = re.sub(r"\b", "", str(text), flags=re.S)
    # удаление лишних цифр из текста
    text = re.sub(r"\d+", "", str(text), flags=re.S)
    # удаление лишних пробелов
    text = re.sub(r" +", " ", str(text), flags=re.S)
    return text

# в идеале, конечно, брать диапазон таблицы кодировки Unicode и оставлять только символы,
# которые в него входят, чтобы не было таких странных токенов, как выше.
def remove_non_latin_letter(text):
    new_text = list()
    for token in text.split(' '):
        if all(map(lambda x:  x <= 122 and x >= 97,  list(token.encode("utf-8")))):
            new_text.append(token)
        else:
            continue
    return ' '.join(new_text)

data['text_prepared'] = (data['text']
                            .apply(remove_punct)
                            .apply(numbers_to_words)
                            .apply(remove_tags)
                            .apply(remove_punct)
                            .apply(remove_non_latin_letter)
                        )
data.head(20)

text  \
0   Curraghglass, an Anglicisation of the Gaelic, ...   
1   Anthony Joshua vs. Andy Ruiz Jr. was a heavywe...   
2   The men's freestyle welterweight competition a...   
3   The Munich-Montserrat Book of Hours is a 1535 ...   
4   Valdó Szűcs (born 29 June 1995) is a Hungarian...   
5   Backstop behind home plate at alt=Half of a ba...   
6   Muhammad Latif (born 13 February 1939) is a Pa...   
7   Hephaestus is the name of a fictional characte...   
8   Wilfred A Randall (1914 – date of death unknow...   
9   John "Jack" Harrison Prescott (fourth ¼ 1890 –...   
10  Bruno Ochman (1929 - 1990) was a Canadian wres...   
11  The Journal of Speech, Language, and Hearing R...   
12  Facundo Nicolás Curuchet (born 21 January 1990...   
13  Devi Singh (born 1926) is an Indian wrestler. ...   
14  Vicente de Paula Mercedes, known as Vicente (b...   
15  Devi Singh can refer to: * Devi Singh (sport s...   
16  On 16 February 1595, a Gaelic Irish force assa...   
17  The Reșița Steam Locomotive Museum is an open-...   
18  Keenan Prochnow (born December 31, 1997) is an...   
19  August from the book's calendar The Da Costa B...   

                                        text_prepared  
0   curraghglass an anglicisation of the gaelic cu...  
1   anthony joshua vs andy ruiz jr was a heavyweig...  
2   the mens freestyle welterweight competition at...  
3   the munichmontserrat book of hours is a one th...  
4   born twentynine june one thousand nine hundred...  
5   backstop behind home plate at althalf of a bas...  
6   muhammad latif born thirteen february one thou...  
7   hephaestus is the name of a fictional characte...  
8   wilfred a randall one thousand nine hundred an...  
9   john jack harrison prescott fourth one thousan...  
10  bruno ochman one thousand nine hundred and twe...  
11  the journal of speech language and hearing res...  
12  facundo curuchet born twentyone january one th...  
13  devi singh born one thousand nine hundred and ...  
14  vicente de paula mercedes known as vicente bor...  
15  devi singh can refer to devi singh sport shoot...  
16  on sixteen february one thousand five hundred ...  
17  the steam locomotive museum is an openair rail...  
18  keenan prochnow born december thirtyone one th...  
19  august from the books calendar the da costa bo...

In [10]:
# после удаления всех символов, которые не попадают в диапазон латинского алфавита в нижнем регистре
# в кодировке Unicode, появились пустые тексты, смотрим пропуски
data[data['text_prepared'] == '']['text_prepared'].count()

6

In [11]:
data.drop(index=data[data['text_prepared'] == ''].index, inplace=True)

In [12]:
#токенизация, лемматизация и удаление стоп-слов
import pymorphy3
from nltk.corpus import stopwords
from functools import lru_cache
from tqdm import tqdm

# кешируем слова для быстрого доступа к ним в других случаях
@lru_cache(maxsize=None) 
def norm_form(word):
    return morph.parse(word)[0].normal_form

lemmatized = list()
morph = pymorphy3.MorphAnalyzer()
for text in tqdm(data['text_prepared']):
    # приведём все слова к нормальной форме и удалим малозначимые слова
    lemmatized.append(' '.join([norm_form(word) for word in text.split(' ') \
                 if word not in stopwords.words('english')]).strip())
data['text_lemmatized'] = lemmatized
data.head(10)

100%|█████████████████████████████████████| 24655/24655 [11:23<00:00, 36.09it/s]


text  \
0  Curraghglass, an Anglicisation of the Gaelic, ...   
1  Anthony Joshua vs. Andy Ruiz Jr. was a heavywe...   
2  The men's freestyle welterweight competition a...   
3  The Munich-Montserrat Book of Hours is a 1535 ...   
4  Valdó Szűcs (born 29 June 1995) is a Hungarian...   
5  Backstop behind home plate at alt=Half of a ba...   
6  Muhammad Latif (born 13 February 1939) is a Pa...   
7  Hephaestus is the name of a fictional characte...   
8  Wilfred A Randall (1914 – date of death unknow...   
9  John "Jack" Harrison Prescott (fourth ¼ 1890 –...   

                                       text_prepared  \
0  curraghglass an anglicisation of the gaelic cu...   
1  anthony joshua vs andy ruiz jr was a heavyweig...   
2  the mens freestyle welterweight competition at...   
3  the munichmontserrat book of hours is a one th...   
4  born twentynine june one thousand nine hundred...   
5  backstop behind home plate at althalf of a bas...   
6  muhammad latif born thirteen february one thou...   
7  hephaestus is the name of a fictional characte...   
8  wilfred a randall one thousand nine hundred an...   
9  john jack harrison prescott fourth one thousan...   

                                     text_lemmatized  
0  curraghglass anglicisation gaelic currach glas...  
1  anthony joshua vs andy ruiz jr heavyweight pro...  
2  mens freestyle welterweight competition one th...  
3  munichmontserrat book hours one thousand five ...  
4  born twentynine june one thousand nine hundred...  
5  backstop behind home plate althalf baseball st...  
6  muhammad latif born thirteen february one thou...  
7  hephaestus name fictional character appearing ...  
8  wilfred randall one thousand nine hundred four...  
9  john jack harrison prescott fourth one thousan...

ТЕКСТ НЕ ЛЕММАТИЗИРОВАН, ПОТОМУ ЧТО PYMORPHY РАБОТАЕТ ТОЛЬКО С РУССКИМ И УКРАИНСКИМ ЯЗЫКАМИ.

In [13]:
# поиск значимых слов/биграмм/триграмм
# сразу используем TF-IDF, чтобы избежать влияния закона Ципфа и найти действительно самые частотные слова
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer_all = TfidfVectorizer(ngram_range=(1,3))

tfidf_matrix_all = vectorizer_all.fit_transform(data["text_lemmatized"])

feature_names_tfidf = vectorizer_all.get_feature_names_out()
feature_names_tfidf

array(['aa', 'aa aa', 'aa aa indicate', ..., 'zzzyva', 'zzzyva two',
       'zzzyva two thousand'], dtype=object)

In [15]:
# !pip install gensim

Defaulting to user installation because normal site-packages is not writeable
DEPRECATION: gpg 1.14.0-unknown has a non-standard version number. pip 24.0 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of gpg or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063


In [18]:
from gensim import corpora
import numpy as np
#  формируем словарь, содержащий количество раз, когда слово появляется в обучающем наборе. 
# При этом словарь фильтруем, и выбираем токены, которые появляются не менее, 
# чем в 1 документе, а также, которые появляются более, чем в 0,8 документах от общего объема корпуса.
data['tokenized'] = data['text_lemmatized'].apply(lambda x: np.array(x.split(' ')))
dictionary = corpora.Dictionary(data['tokenized'])
dictionary.filter_extremes(no_below=1, no_above=0.8)

In [22]:
from gensim import models
# для каждого документа мы создаем словарь, в котором хранится информация, 
# какое слово сколько раз встречается
corpus = [dictionary.doc2bow(text) for text in data['tokenized']]
lda = models.LdaModel(corpus, num_topics=40, id2word=dictionary)
lda.show_topics(10)

[(1,
  '0.119*"japan" + 0.090*"japanese" + 0.028*"tokyo" + 0.027*"baltimore" + 0.023*"prefecture" + 0.018*"massachusetts" + 0.013*"categoryjapanese" + 0.012*"haitian" + 0.010*"nova" + 0.009*"candle"'),
 (0,
  '0.138*"de" + 0.050*"la" + 0.031*"san" + 0.024*"el" + 0.020*"del" + 0.016*"spanish" + 0.014*"mexico" + 0.012*"two" + 0.012*"province" + 0.012*"spain"'),
 (29,
  '0.057*"nine" + 0.015*"art" + 0.014*"two" + 0.014*"new" + 0.012*"york" + 0.011*"museum" + 0.008*"work" + 0.007*"american" + 0.006*"book" + 0.006*"published"'),
 (28,
  '0.056*"two" + 0.025*"players" + 0.019*"season" + 0.017*"football" + 0.017*"nine" + 0.017*"league" + 0.014*"team" + 0.010*"club" + 0.010*"first" + 0.009*"played"'),
 (35,
  '0.024*"two" + 0.012*"john" + 0.009*"valigntop" + 0.007*"david" + 0.007*"michael" + 0.007*"pa" + 0.006*"smith" + 0.006*"three" + 0.006*"brown" + 0.006*"norton"'),
 (10,
  '0.024*"two" + 0.024*"nine" + 0.015*"eight" + 0.015*"district" + 0.012*"party" + 0.010*"election" + 0.010*"state" + 0.

In [25]:
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis

pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda, corpus, dictionary=lda.id2word)
vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
34     0.165278  0.050268       1        1  9.373769
28     0.094629 -0.017373       2        1  6.644412
24    -0.206599 -0.038944       3        1  5.344468
11    -0.200664  0.060908       4        1  5.020059
29    -0.059064 -0.050071       5        1  4.650556
33    -0.207271  0.031788       6        1  4.552359
14    -0.071674 -0.196639       7        1  4.199150
8     -0.099614  0.025261       8        1  4.073929
15    -0.130689 -0.157236       9        1  3.870028
36     0.228816 -0.010580      10        1  3.677081
10    -0.047111  0.077188      11        1  3.582455
32    -0.225806  0.009316      12        1  3.527825
21    -0.007120 -0.210731      13        1  3.081441
27    -0.045089  0.090798      14        1  2.864083
20    -0.225288 -0.032839      15        1  2.789583
2     -0.190132 -0.002470      16        1  2.708924
13    -0.084367  0.016605      17        1  2.236685
6      0.055218  0.072362      18        1  2.129321
35     0.100926 -0.149376      19        1  1.932599
31     0.013023 -0.242449      20        1  1.778594
16     0.208773  0.031809      21        1  1.747618
37     0.065565 -0.096793      22        1  1.712818
7     -0.093275  0.087238      23        1  1.682824
23    -0.005999  0.156423      24        1  1.570081
26     0.132639 -0.027803      25        1  1.508555
30    -0.033145  0.137112      26        1  1.485673
19    -0.114066  0.077781      27        1  1.467095
0      0.024031  0.040771      28        1  1.257281
5      0.195599 -0.025900      29        1  1.200634
38    -0.034090 -0.056994      30        1  1.114152
4      0.033572  0.169966      31        1  0.944088
3      0.192617 -0.013089      32        1  0.926418
22     0.089250  0.067797      33        1  0.915764
9      0.071873  0.067910      34        1  0.840049
12    -0.017033  0.095500      35        1  0.696516
18     0.163187 -0.016189      36        1  0.687749
25     0.039539 -0.102572      37        1  0.682648
39     0.150358  0.037336      38        1  0.679760
17     0.069792  0.060481      39        1  0.565843
1      0.003412 -0.016570      40        1  0.277114, topic_info=             Term           Freq          Total Category  logprob  loglift
223   aligncenter   39740.000000   39740.000000  Default  30.0000  30.0000
122          nine  184110.000000  184110.000000  Default  29.0000  29.0000
810     alignleft   24165.000000   24165.000000  Default  28.0000  28.0000
744           two  202282.000000  202282.000000  Default  27.0000  27.0000
826            de   16102.000000   16102.000000  Default  26.0000  26.0000
...           ...            ...            ...      ...      ...      ...
307          city     162.668734   11081.229258  Topic40  -4.8775   1.6672
122          nine     175.615617  184110.542657  Topic40  -4.8009  -1.0665
1456         best     120.434535    6264.160989  Topic40  -5.1781   1.9370
744           two     142.371785  202282.629810  Topic40  -5.0108  -1.3705
542           new      94.669073   26928.122490  Topic40  -5.4188   0.2380

[3253 rows x 6 columns], token_table=       Topic      Freq   Term
term                         
913        1  0.009246  abbey
913        5  0.033901  abbey
913        6  0.003082  abbey
913        8  0.012327  abbey
913       11  0.009246  abbey
...      ...       ...    ...
32711     13  0.005142   zhou
32711     19  0.005142   zhou
32711     22  0.971870   zhou
34488      1  0.088669   zinc
34488     23  0.904426   zinc

[28761 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[35, 29, 25, 12, 30, 34, 15, 9, 16, 37, 11, 33, 22, 28, 21, 3, 14, 7, 36, 32, 17, 38, 8, 24, 27, 31, 20, 1, 6, 39, 5, 4, 23, 10, 13, 19, 26, 40, 18, 2])